## Imports

In [1]:
%load_ext autoreload
%autoreload 2

import re
import urllib.request
api_url = 'https://raw.githubusercontent.com/tanmayyb/ele70_bv03/refs/heads/main/api/datasets.py'
exec(urllib.request.urlopen(api_url).read())

## Load Datasets and Preprocess

In [2]:
load_offline = True

In [3]:
if not load_offline:
  ieso_dataset = load_ieso_dataset(2010, 2020, join=True).iloc[:-1]
  ieso_dataset.to_csv('./data/ieso_dataset.csv', index=False)
else:
  ieso_dataset = pd.read_csv('./data/ieso_dataset.csv')
  ieso_dataset.DateTime = pd.to_datetime(ieso_dataset.DateTime)

In [4]:
if not load_offline:
  weather_dataset = load_climate_dataset(2010, 2020, join=True).iloc[1:]
  weather_dataset.to_csv('./data/weather_dataset.csv', index=False)
else:
  weather_dataset = pd.read_csv('./data/weather_dataset.csv')
  weather_dataset.DateTime = pd.to_datetime(weather_dataset.DateTime)

C:\Users\tanma\AppData\Local\Temp\ipykernel_15872\598990861.py:5: DtypeWarning: Columns (10,12,14,16,24) have mixed types. Specify dtype option on import or set low_memory=False.
  weather_dataset = pd.read_csv('./data/weather_dataset.csv')


In [5]:
#@markdown merge and preprocess

dataset = pd.merge(ieso_dataset, weather_dataset, on="DateTime")

def preprocess(dataset:pd.DataFrame, split_datetime=True) -> pd.DataFrame:
  df = dataset.copy()
  ieso_cols = ['Toronto']
  climate_cols = [
       'Temp (°C)',
      #  'Temp Flag',
       'Dew Point Temp (°C)',
      #  'Dew Point Temp Flag',
       'Rel Hum (%)',
      #  'Rel Hum Flag',
       'Precip. Amount (mm)',
      #  'Precip. Amount Flag',
      #  'Wind Dir (10s deg)',
      #  'Wind Dir Flag',
      #  'Wind Spd (km/h)',
      #  'Wind Spd Flag',
      #  'Visibility (km)',
      #  'Visibility Flag',
       'Stn Press (kPa)',
      #  'Stn Press Flag',
       'Hmdx',
      #  'Hmdx Flag', 'Wind Chill', 'Wind Chill Flag', 'Weather'
      ]
  if split_datetime:
    df['Y'] = df['DateTime'].dt.year
    df['M'] = df['DateTime'].dt.month
    df['D'] = df['DateTime'].dt.day
    df['H'] = df['DateTime'].dt.hour
    cols = ['Y', 'M', 'D', 'H']
  else:
    cols = ['DateTime']

  # delete leap day
  df = df[~((df.DateTime.dt.month == 2) & (df.DateTime.dt.day == 29))]
  dt = df['DateTime'] # store datettime

  cols += ieso_cols+climate_cols

  df = df[cols]

  # make columns names better
  df.columns = df.columns.str.replace('.', '')
  df.columns = df.columns.str.replace(' ', '')
  df.columns = df.columns.str.replace(r"\(.*?\)", "", regex=True)

  nans = df.isna().sum().to_dict()

  # dirty mean imputation
  data = df.fillna(df.mean())

  # # dirty -1 imputation
  # data = df.fillna(pd.Series(index=df.columns, data=[-1.0]*len(df.columns)))

  data = data.reset_index()

  return df, nans, dt

df, nans, dt = preprocess(dataset)

```
RelHum -> 0-100 norm
Hmdx-> 0-100 norm
Toronto -> mean norm
Temp -> mean norm
DewPointTemp -> mean norm
PrecipAmount -> mean norm
StnPress -> mean norm
```

In [6]:
df

Y   M   D   H  Toronto  Temp  DewPointTemp  RelHum  PrecipAmount  \
0      2010   1   1   1     4966   2.4           1.7    95.0           NaN   
1      2010   1   1   2     4761   2.1           1.4    95.0           NaN   
2      2010   1   1   3     4594   2.0           1.4    96.0           NaN   
3      2010   1   1   4     4443   1.7           1.2    96.0           NaN   
4      2010   1   1   5     4375   1.5           1.1    97.0           NaN   
...     ...  ..  ..  ..      ...   ...           ...     ...           ...   
96426  2020  12  31  19     6123   1.9          -3.8    66.0           0.0   
96427  2020  12  31  20     5948   2.0          -3.8    65.0           0.0   
96428  2020  12  31  21     5741   2.2          -3.7    65.0           0.0   
96429  2020  12  31  22     5527   2.1          -3.9    65.0           0.0   
96430  2020  12  31  23     5301   1.8          -4.1    65.0           0.0   

       StnPress  Hmdx  
0           NaN   NaN  
1           NaN   NaN  
2           NaN   NaN  
3           NaN   NaN  
4           NaN   NaN  
...         ...   ...  
96426    100.98   NaN  
96427    101.06   NaN  
96428    101.13   NaN  
96429    101.23   NaN  
96430    101.28   NaN  

[96359 rows x 11 columns]

In [7]:
def create_train_test_split(dataset:pd.DataFrame, target:str='target', split_coeff:float=0.8, dt=None) -> tuple:
  training_cutoff = int(split_coeff*len(dataset))
  train = dataset.iloc[:training_cutoff]
  test = dataset.iloc[training_cutoff:]

  X_train = train.drop(columns=[target])
  y_train = train[target]
  X_test = test.drop(columns=[target])
  y_test = test[target]

  (train_idx, test_idx) = None, None
  if dt is not None:
    train_idx = dt[:training_cutoff]
    test_idx = dt[training_cutoff:]

  return (X_train, X_test, y_train, y_test), (train_idx, test_idx)

target = 'Toronto'
(X_train, X_test, y_train, y_test), (train_idx, test_idx) = create_train_test_split(df, target=target, dt=dt)
y_test_numpy = y_test.to_numpy()

## Visualize XGBoost Learning

In [8]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import xgboost as xgb
from xgboost import plot_importance, plot_tree
from sklearn.metrics import mean_squared_error, mean_absolute_error
import matplotlib.pyplot as plt

In [9]:
# # Load the saved model
# model = xgb.Booster()
# model.load_model('./outputs/xgb_mt1r1_model.json')

# # Create a figure with larger size
# plt.figure(figsize=(20,10))

# # Plot feature importance
# xgb.plot_importance(model)
# plt.title('Feature Importance in XGBoost Model')
# plt.tight_layout()
# plt.show()

# # Plot the tree with better visibility
# plt.figure(figsize=(30, 20))  # More balanced aspect ratio
# xgb.plot_tree(model, 
#               num_trees=0,
#               rankdir='LR',    # Left to right layout
#               ax=plt.gca()     # Get current axis
#               )
# plt.title('First Decision Tree in XGBoost Model', fontsize=16)
# plt.tight_layout()
# plt.savefig('./outputs/xgb_mt1r1_trees.png', dpi=300, bbox_inches='tight')
# plt.show()

## XGBoost Regression Model - Grid Search

In [10]:
# # https://www.kaggle.com/code/robikscube/tutorial-time-series-forecasting-with-xgboost#Create-XGBoost-Model
# reg = xgb.XGBRegressor(n_estimators=1000)
# reg.fit(X_train, y_train,
#         eval_set=[(X_train, y_train), (X_test, y_test)],
#         # early_stopping_rounds=50,
#        verbose=False)

In [12]:
# pred = reg.predict(X_test)

In [13]:
from sklearn.model_selection import GridSearchCV
from tqdm import tqdm

# Define parameter grid with reduced search space
param_grid = {
    'max_depth': [3, 5],
    'learning_rate': [0.01, 0.1],
    'n_estimators': [100, 500],
    'min_child_weight': [1, 3],
    'subsample': [0.8, 1.0],
    'colsample_bytree': [0.8, 1.0],
    'gamma': [0, 0.1]
}

# Create base model
xgb_model = xgb.XGBRegressor()

from tqdm.notebook import tqdm
import time

# Initialize GridSearchCV with progress bar
grid_search = GridSearchCV(
    estimator=xgb_model,
    param_grid=param_grid,
    cv=5,
    scoring='neg_mean_squared_error',
    verbose=0,  # Reduce verbosity since we'll use tqdm
    n_jobs=2    # Reduce number of parallel jobs to avoid overwhelming CPU
)

# Wrap the fit process in tqdm
with tqdm(total=1) as pbar:
    grid_search.fit(X_train, y_train)
    pbar.update(1)

# Print best parameters and score
print("Best parameters:", grid_search.best_params_)
print("Best MSE:", -grid_search.best_score_)

# Use best model for predictions
best_model = grid_search.best_estimator_
pred = best_model.predict(X_test)

  0%|          | 0/1 [00:00<?, ?it/s]

Best parameters: {'colsample_bytree': 0.8, 'gamma': 0, 'learning_rate': 0.1, 'max_depth': 5, 'min_child_weight': 3, 'n_estimators': 100, 'subsample': 0.8}
Best MSE: 224884.0125


In [16]:
def get_models_from_grid_search(grid_search, n_models=3):
    # Get all results from grid search
    results = pd.DataFrame(grid_search.cv_results_)
    
    # Sort by mean test score
    results = results.sort_values('mean_test_score', ascending=False)
    
    # Get parameters for best and worst models
    model_params = results['params'].head(n_models).tolist()
    
    # Create and fit models
    models = {}
    for i, params in enumerate(model_params):
        if i == 0:
            model_name = 'Best Model'
        else:
            model_name = f'Model {i+1}'
        
        model = xgb.XGBRegressor(**params)
        model.fit(X_train, y_train)
        models[model_name] = model
    
    return models

# Get multiple models
models = get_models_from_grid_search(grid_search, n_models=3)

# Generate predictions for each model
predictions_dict = {
    name: model.predict(X_test) 
    for name, model in models.items()
}

# Now we can use the existing plotting function
fig, metrics_df = plot_model_comparisons(test_idx, y_test, predictions_dict)
fig.show()
print("\nModel Performance Metrics:")
print(metrics_df)

# Save the comparison plot
fig.write_html('./outputs/model_comparisons.html')

C:\Users\tanma\AppData\Local\Temp\ipykernel_15872\923481934.py:50: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.




Model Performance Metrics:
        Model            MSE         MAE      MAPE
0  Best Model  156027.218750  303.666046  5.437529
0     Model 2  156027.218750  303.666046  5.437529
0     Model 3  157586.578125  305.211395  5.468611


In [14]:
#@markdown plot multiple model predictions
from plotly import graph_objects as go
from plotly.subplots import make_subplots

def plot_model_comparisons(test_idx, y_test, predictions_dict):
    """
    Plot predictions from multiple models
    Args:
        test_idx: datetime index for test data
        y_test: actual test values
        predictions_dict: dictionary of model predictions {model_name: predictions}
    """
    # Create main prediction plot
    fig = go.Figure()
    
    # Plot actual values
    fig.add_trace(go.Scattergl(
        x=test_idx,
        y=y_test,
        name='Actual',
        line_color='blue'
    ))
    
    # Plot each model's predictions
    colors = ['red', 'green', 'orange', 'purple', 'brown']  # Add more colors if needed
    for (model_name, pred), color in zip(predictions_dict.items(), colors):
        fig.add_trace(go.Scattergl(
            x=test_idx,
            y=pred,
            name=f'{model_name}',
            line_color=color
        ))
    
    fig.update_layout(
        title="Time Series Forecasting - Model Comparisons",
        xaxis_title="Time",
        yaxis_title="Energy Demand",
        template="plotly_white",
        xaxis=dict(rangeslider=dict(visible=True))
    )
    
    # Create metrics comparison table
    metrics_df = pd.DataFrame(columns=['Model', 'MSE', 'MAE', 'MAPE'])
    
    for model_name, pred in predictions_dict.items():
        mse = mean_squared_error(y_test, pred)
        mae = mean_absolute_error(y_test, pred)
        mape = mean_absolute_percentage_error(y_test, pred)
        
        metrics_df = pd.concat([metrics_df, pd.DataFrame({
            'Model': [model_name],
            'MSE': [mse],
            'MAE': [mae],
            'MAPE': [mape]
        })])
    
    return fig, metrics_df

# Example usage:
predictions_dict = {
    'XGBoost': pred,  # your existing XGBoost predictions
    'Model2': model2_predictions,  # add other model predictions
    'Model3': model3_predictions,
}

fig, metrics_df = plot_model_comparisons(test_idx, y_test, predictions_dict)
fig.show()
print("\nModel Performance Metrics:")
print(metrics_df)

# Save the comparison plot
fig.write_html('./outputs/model_comparisons.html')

NameError: name 'model2_predictions' is not defined

## Results and Analysis

In [ ]:
#@markdown plot prediction
from plotly import graph_objects as go
fig = go.Figure()
fig.add_trace(go.Scattergl(
    x=test_idx,
    y=y_test.to_numpy(),
    name='Actual',
    line_color='blue')
)

fig.add_trace(go.Scattergl(
    x=test_idx,
    y=pred,
    name='Predicted',
    line_color='red')
)


# Set the theme to 'plotly_white'
fig.update_layout(
    title=f"Time Series Forecasting for {target} with XGBoostRegressor",
    xaxis_title="t (1 unit = 1 hour)",
    yaxis_title="Energy Demand",
    template="plotly_white",
    xaxis = dict( rangeslider=dict(
      visible=True
    ))
)
fig.show()
# fig.write_html(f'mcr4_xgb_mt1r1_pred.html')

In [15]:
#@markdown calculate MSE, MAE, MAPE
mse = mean_squared_error(y_true=y_test,
                   y_pred=pred)

mae = mean_absolute_error(y_true=y_test,
                   y_pred=pred)

def mean_absolute_percentage_error(y_true, y_pred):
    """Calculates MAPE given y_true and y_pred"""
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

print(f"MSE: {mse}")
print(f"MAE: {mae}")
print(f"MAPE: {mean_absolute_percentage_error(y_test, pred)}")

MSE: 156027.21875
MAE: 303.6660461425781
MAPE: 5.437528972247017


In [ ]:
#@markdown top 10 worst predictions
tmp = pd.concat([dt, y_test, pd.Series(pred, index=y_test.index, name='pred')],
                axis=1).dropna()

tmp['error'] = tmp[target] - tmp['pred']
tmp['abs_error'] = tmp['error'].apply(np.abs)

worst_predicted = tmp.sort_values(by='abs_error', ascending=False)
worst_predicted[:10]

In [ ]:
#@markdown top 10 best predictions
best_predicted = tmp.sort_values(by='abs_error', ascending=True)
best_predicted[:10]

In [ ]:
best_predicted.iloc[:168].sort_index()

In [ ]:
#@markdown plot best/worst predictions
from plotly.subplots import make_subplots

hours = 168*10 # hours in a week
sorted_best_predicted = best_predicted.iloc[:hours].sort_index()
sorted_worst_predicted = worst_predicted.iloc[:hours].sort_index()


fig = make_subplots(rows=2, cols=1, shared_xaxes=True, subplot_titles=(f'Best Predicted Hours for {target}',f'Worst Predicted Hours for {target}'))

# best predicted
fig.append_trace(go.Scattergl(
    x=sorted_best_predicted.DateTime,
    y=sorted_best_predicted[target],
    name='Target',
    mode='markers',
    # line_color='blue'
), row=1, col=1)

fig.append_trace(go.Scattergl(
    x=sorted_best_predicted.DateTime,
    y=sorted_best_predicted[target],
    name='Predicted',
    line_color='red'
), row=1, col=1)


# worst predicted
fig.append_trace(go.Scattergl(
    x=sorted_worst_predicted.DateTime,
    y=sorted_worst_predicted[target],
    name='Target',
    mode='markers',
    # line_color='blue'
), row=2, col=1)

fig.append_trace(go.Scattergl(
    x=sorted_worst_predicted.DateTime,
    y=sorted_worst_predicted.pred,
    name='Predicted',
    line_color='red'
), row=2, col=1)


fig.update_layout(
    title=f"Best/Worst Predictions for: {target}",

    # yaxis_title="Energy Demand",
    template="plotly_white",
)

fig.update_xaxes(
    title="t (1 unit = 1 hour)",
    rangeslider_visible=True, row=2, col=1)


# https://stackoverflow.com/questions/77370313/plotting-subplots-with-a-shared-slider-in-python
fig.show()
fig.write_html(f'./outputs/xgb_mt1r1_pred_eval.html')


## Wrapping Up

In [23]:
# save as csv for anomaly detection
tmp.to_csv('./outputs/xgb_mt1r1_pred_eval.csv')

In [22]:
# save learned model
reg.save_model('./outputs/xgb_mt1r1_model.json')  # Save model in JSON format

In [18]:
#@markdown wandb code for later

# !pip install wandb
# wandb login

# wandb.init(
#     # set the wandb project where this run will be logged
#     project="my-awesome-project",

#     # track hyperparameters and run metadata
#     config={
#     "learning_rate": 0.02,
#     "architecture": "CNN",
#     "dataset": "CIFAR-100",
#     "epochs": 10,
#     }
# )

# # simulate training
# epochs = 10
# offset = random.random() / 5
# for epoch in range(2, epochs):
#     acc = 1 - 2 ** -epoch - random.random() / epoch - offset
#     loss = 2 ** -epoch + random.random() / epoch + offset

#     # log metrics to wandb
#     wandb.log({"acc": acc, "loss": loss})

# # [optional] finish the wandb run, necessary in notebooks
# wandb.finish()